#SoMe Topic Modeling Notebook | Release canvas 1 📖

## Installations and Libraries 💽

In [44]:
# Installations
import sys
if 'google.colab' in sys.modules:
    !pip install emoji --upgrade
    !pip install pandas-profiling==2.*
    !pip install plotly==4.*
    !python -m spacy download en_core_web_lg
    !pip install pyldavis
    !pip install gensim
    #!pip install --upgrade autopep8

Requirement already up-to-date: emoji in /usr/local/lib/python3.6/dist-packages (0.5.4)
✔ Download and installation successful
You can now load the model via spacy.load('en_core_web_lg')


In [0]:
# Required Libraries

#Base and Cleaning 
import json
import requests
import pandas as pd
import numpy as np
import emoji
import regex
import re
import string
from collections import Counter
import time 

#Visualizations
import plotly.express as px
import seaborn as sns
import matplotlib as plt 
import pyLDAvis.gensim

#Natural Language Processing (NLP)
import spacy
from spacy.tokenizer import Tokenizer
from gensim.corpora import Dictionary
from gensim.models.ldamulticore import LdaMulticore
from gensim.models.coherencemodel import CoherenceModel
from gensim.parsing.preprocessing import STOPWORDS as SW
from wordcloud import STOPWORDS
stopwords = set(STOPWORDS)

##Data Cleaning 🧹

In [46]:
# Loading the JSON file 
url_elon = 'https://raw.githubusercontent.com/Lambda-School-Labs/social-media-strategy-ds/feature/topic/python_notebooks/elonmusk_followers_english.json'
url_dutchbros = 'https://raw.githubusercontent.com/Lambda-School-Labs/social-media-strategy-ds/feature/topic/python_notebooks/dutchbros_followers.json'

df = requests.get(url_elon).json()

# Converting the dataset to pandas DataFrame and renaming the columns 
df = pd.DataFrame(df.values())
df = df.rename(columns={0:'original_tweets'})

#Removing emojies from text
#Refrence 1 : https://stackoverflow.com/questions/33404752/removing-emojis-from-a-string-in-python
#Refrence 2 : https://stackoverflow.com/questions/11331982/how-to-remove-any-url-within-a-string-in-python

def give_emoji_free_text(text):
    """
    Removes emoji's from tweets
    Accepts:
        Text (tweets)
    Returns:
        Text (emoji free tweets)
    """
    emoji_list = [c for c in text if c in emoji.UNICODE_EMOJI]
    clean_text = ' '.join([str for str in text.split() if not any(i in str for i in emoji_list)])
    return clean_text

def url_free_text(text):
    '''
    Cleans text from urls
    '''
    text = re.sub(r'http\S+', '', text)
    return text

# Apply the function above and get tweets free of emoji's
call_emoji_free = lambda x: give_emoji_free_text(x)

# Apply `call_emoji_free` which calls the function to remove all emoji's
df['emoji_free_tweets'] = df['original_tweets'].apply(call_emoji_free)

#Create a new column with url free tweets
df['url_free_tweets'] = df['emoji_free_tweets'].apply(url_free_text)

df

original_tweets  ...                                    url_free_tweets
0     This kid will forever be a legend 😂 https://t....  ...                 This kid will forever be a legend 
1     If you truly believe Lebrons mindset, competit...  ...  If you truly believe Lebrons mindset, competit...
2       BUTTLICKER! OUR PRICES HAVE NEVER BEEN LOWER!!!  ...    BUTTLICKER! OUR PRICES HAVE NEVER BEEN LOWER!!!
3                                      @Bhuvan_Bam ❤️❤️  ...                                        @Bhuvan_Bam
4     I'm not crying you're crying.\nhttps://t.co/Bc...  ...                     I'm not crying you're crying. 
...                                                 ...  ...                                                ...
9941  @MirandaSleeper The offerings in that f-3 are ...  ...  @MirandaSleeper The offerings in that f-3 are ...
9942  This will be the defining segment of “The Last...  ...  This will be the defining segment of “The Last...
9943  @frank_miskelly I don’t like it, I LOVE IT! Bu...  ...  @frank_miskelly I don’t like it, I LOVE IT! Bu...
9944  Excited for my brother @Shufly10 as he embarks...  ...  Excited for my brother @Shufly10 as he embarks...
9945  Congrats to @shufly10 on being named offensive...  ...  Congrats to @shufly10 on being named offensive...

[9946 rows x 3 columns]

##Topic Modeling ㊙️

###Tokenizing 🕵🏻‍♂

In [0]:
# Load spacy
# Make sure to restart the runtime after running installations and libraries tab
nlp = spacy.load('en_core_web_lg')


In [48]:
"""
Import Gensim and Wordcloud to use their stopwords as well and use the combined stopwords of ALL as the variable:
ALL_STOP_WORDS
"""
# Timing Start
program_start_time = time.time()

# Tokenizer
tokenizer = Tokenizer(nlp.vocab)


# Custom stopwords
custom_stopwords = ['hi','\n','\n\n', '&amp;', ' ', '.', '-', 'got', "it's", 'it’s', "i'm", 'i’m', 'im', 'want', 'like', '$', '@']

# Customize stop words by adding to the default list
STOP_WORDS = nlp.Defaults.stop_words.union(custom_stopwords)

# ALL_STOP_WORDS = spacy + gensim + wordcloud
ALL_STOP_WORDS = STOP_WORDS.union(SW).union(stopwords)


tokens = []

for doc in tokenizer.pipe(df['url_free_tweets'], batch_size=500):
    doc_tokens = []    
    for token in doc: 
        if token.text.lower() not in STOP_WORDS:
            doc_tokens.append(token.text.lower())   
    tokens.append(doc_tokens)

# Makes tokens column
df['tokens'] = tokens

# Timing End
program_end_time = time.time()

# View df
df

original_tweets  ...                                             tokens
0     This kid will forever be a legend 😂 https://t....  ...                             [kid, forever, legend]
1     If you truly believe Lebrons mindset, competit...  ...  [truly, believe, lebrons, mindset,, competitiv...
2       BUTTLICKER! OUR PRICES HAVE NEVER BEEN LOWER!!!  ...                    [buttlicker!, prices, lower!!!]
3                                      @Bhuvan_Bam ❤️❤️  ...                                      [@bhuvan_bam]
4     I'm not crying you're crying.\nhttps://t.co/Bc...  ...                          [crying, you're, crying.]
...                                                 ...  ...                                                ...
9941  @MirandaSleeper The offerings in that f-3 are ...  ...  [@mirandasleeper, offerings, f-3, closed, prev...
9942  This will be the defining segment of “The Last...  ...                 [defining, segment, “the, dance.”]
9943  @frank_miskelly I don’t like it, I LOVE IT! Bu...  ...  [@frank_miskelly, don’t, it,, love, it!, think...
9944  Excited for my brother @Shufly10 as he embarks...  ...  [excited, brother, @shufly10, embarks, new, jo...
9945  Congrats to @shufly10 on being named offensive...  ...  [congrats, @shufly10, named, offensive, coordi...

[9946 rows x 4 columns]

In [49]:
# See how long it took
print(program_end_time - program_start_time, "seconds to finish")

1.7005128860473633 seconds to finish


###Lemmatization🇬🇧

In [0]:
# Refrence 4 : https://stackoverflow.com/questions/45306988/column-of-lists-convert-list-to-string-as-a-new-column

# Timing Start
program_start_time = time.time()

# Make tokens a string again
df['tokens_back_to_text'] = [' '.join(map(str, l)) for l in df['tokens']]

def get_lemmas(text):
    '''Used to lemmatize the processed tweets'''
    lemmas = []
    
    doc = nlp(text)
    
    # Something goes here :P
    for token in doc: 
        if ((token.is_stop == False) and (token.is_punct == False)) and (token.pos_ != 'PRON'):
            lemmas.append(token.lemma_)
    
    return lemmas

df['lemmas'] = df['tokens_back_to_text'].apply(get_lemmas)

# Make lemmas a string again
df['lemmas_back_to_text'] = [' '.join(map(str, l)) for l in df['lemmas']]
# df[['original_tweet', 'lemmas_back_to_text']]

# Timing End
program_end_time = time.time()


In [51]:
#Printing Lemmetization Time
print(program_end_time - program_start_time, "seconds to finish")

76.06071639060974 seconds to finish


In [52]:
# Timing Start
program_start_time = time.time()

# Tokenizer
tokenizer = Tokenizer(nlp.vocab)

# Tokenizer function
def tokenize(text):
    """
    Parses a string into a list of semantic units (words)
    Args:
        text (str): The string that the function will tokenize.
    Returns:
        list: tokens parsed out
    """
    # Removing url's
    pattern = r"http\S+"
    
    tokens = re.sub(pattern, "", text) # https://www.youtube.com/watch?v=O2onA4r5UaY
    tokens = re.sub('[^a-zA-Z 0-9]', '', text)
    tokens = re.sub('[%s]' % re.escape(string.punctuation), '', text) # Remove punctuation
    tokens = re.sub('\w*\d\w*', '', text) # Remove words containing numbers
    tokens = re.sub('@*!*\$*', '', text) # Remove @ ! $
    tokens = tokens.strip(',') # TESTING THIS LINE
    tokens = tokens.strip('?') # TESTING THIS LINE
    tokens = tokens.strip('!') # TESTING THIS LINE
    tokens = tokens.strip("'") # TESTING THIS LINE
    tokens = tokens.strip(".") # TESTING THIS LINE

    tokens = tokens.lower().split() # Make text lowercase and split it
    
    return tokens

# Apply tokenizer
df['lemma_tokens'] = df['lemmas_back_to_text'].apply(tokenize)

# Timing End
program_end_time = time.time()

# View those tokens (the 4th column)
df

<input>:22: DeprecationWarning:

invalid escape sequence \w

<input>:22: DeprecationWarning:

invalid escape sequence \w

<input>:22: DeprecationWarning:

invalid escape sequence \w

<input>:22: DeprecationWarning:

invalid escape sequence \w

<input>:23: DeprecationWarning:

invalid escape sequence \$

<input>:22: DeprecationWarning:

invalid escape sequence \w

<input>:23: DeprecationWarning:

invalid escape sequence \$

<input>:22: DeprecationWarning:

invalid escape sequence \w

<input>:23: DeprecationWarning:

invalid escape sequence \$

<input>:22: DeprecationWarning:

invalid escape sequence \w

<input>:23: DeprecationWarning:

invalid escape sequence \$

<input>:22: DeprecationWarning:

invalid escape sequence \w

<input>:23: DeprecationWarning:

invalid escape sequence \$

<input>:22: DeprecationWarning:

invalid escape sequence \w

<input>:23: DeprecationWarning:

invalid escape sequence \$

<input>:22: DeprecationWarning:

invalid escape sequence \w

<input>:23: DeprecationW

original_tweets  ...                                       lemma_tokens
0     This kid will forever be a legend 😂 https://t....  ...                             [kid, forever, legend]
1     If you truly believe Lebrons mindset, competit...  ...  [truly, believe, lebrons, mindset, competitive...
2       BUTTLICKER! OUR PRICES HAVE NEVER BEEN LOWER!!!  ...                         [buttlicker, price, lower]
3                                      @Bhuvan_Bam ❤️❤️  ...                                       [bhuvan_bam]
4     I'm not crying you're crying.\nhttps://t.co/Bc...  ...                                         [cry, cry]
...                                                 ...  ...                                                ...
9941  @MirandaSleeper The offerings in that f-3 are ...  ...  [mirandasleeper, offering, f-3, close, previou...
9942  This will be the defining segment of “The Last...  ...                           [define, segment, dance]
9943  @frank_miskelly I don’t like it, I LOVE IT! Bu...  ...  [frank_miskelly, love, think, sixth, old, run,...
9944  Excited for my brother @Shufly10 as he embarks...  ...  [excited, brother, shufly10, embark, new, jour...
9945  Congrats to @shufly10 on being named offensive...  ...  [congrats, shufly10, name, offensive, coordina...

[9946 rows x 8 columns]

In [53]:
#Printing Tokenization Time
print(program_end_time - program_start_time, "seconds to finish")


0.3407933712005615 seconds to finish


###id2word 📒

In [54]:
# Create a id2word dictionary
id2word = Dictionary(df['lemma_tokens'])
print(len(id2word))

21883


In [55]:
# Filtering Extremes
id2word.filter_extremes(no_below=2, no_above=.99)
print(len(id2word))

8229


###Corpus Object & Generating Base Model Topics 📚

In [0]:
# Creating a corpus object 
corpus = [id2word.doc2bow(d) for d in df['lemma_tokens']]

####Base Model

In [57]:
# Timing Start
base_model_program_start_time = time.time()

# Instantiating a LDA model 
model = LdaMulticore(corpus=corpus, num_topics=5, id2word=id2word, workers=12, passes=5)

# Timing End
base_model_program_end_time = time.time()


Streaming output truncated to the last 5000 lines.

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.

/usr/local/lib/python3.6/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.

/usr/local/lib/python3.6/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.

/usr/local/lib/python3.6/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.

/usr/local/lib/python3.6/dist-pa

In [58]:
#Printing First Model Time
base_model_runtime = round(base_model_program_end_time - base_model_program_start_time, 2)
print(base_model_runtime)


25.250271320343018


In [0]:
# Filtering for words 
words = [re.findall(r'"([^"]*)"',t[1]) for t in model.print_topics()]


In [0]:
# Create Topics
topics = [' '.join(t[0:10]) for t in words]


In [61]:
# Getting the topics
for id, t in enumerate(topics): 
    print(f"------ Topic {id} ------")
    print(t, end="\n\n")


------ Topic 0 ------
people trump president need realdonaldtrump come say good work help

------ Topic 1 ------
know day new love happy good look try biden year

------ Topic 2 ------
time follow good retweet people know giveaway work big thank

------ Topic 3 ------
time think go people bitcoin let come today state new

------ Topic 4 ------
obamagate obama day think death tweet 3 say year rt



In [62]:
# Compute Perplexity
# a measure of how good the model is. lower the better
base_perplexity = model.log_perplexity(corpus)
print('\nPerplexity: ', base_perplexity) 

# Compute Coherence Score
coherence_model = CoherenceModel(model=model, texts=df['lemma_tokens'], 
                                   dictionary=id2word, coherence='c_v')
coherence_lda_model_base = coherence_model.get_coherence()
print('\nCoherence Score: ', coherence_lda_model_base)


Streaming output truncated to the last 5000 lines.

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.

/usr/local/lib/python3.6/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.

/usr/local/lib/python3.6/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.

/usr/local/lib/python3.6/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.

/usr/local/lib/python3.6/dist-pa


Perplexity:  -8.453721220210504

Coherence Score:  0.17176779993227603


#### Base Model Topic Distance Visualization 📈

In [63]:
#Creating Topic Distance Visualization 
pyLDAvis.enable_notebook()
pyLDAvis.gensim.prepare(model, corpus, id2word)

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
0     -0.007066  0.045622       1        1  23.074215
3     -0.011121  0.032772       2        1  22.700338
2     -0.058363 -0.095098       3        1  18.543205
1      0.109591 -0.030228       4        1  18.169455
4     -0.033042  0.046932       5        1  17.512789, topic_info=          Term        Freq       Total Category  logprob  loglift
210     follow  297.000000  297.000000  Default  30.0000  30.0000
791    retweet  201.000000  201.000000  Default  29.0000  29.0000
802  obamagate  180.000000  180.000000  Default  28.0000  28.0000
117       time  486.000000  486.000000  Default  27.0000  27.0000
36        know  437.000000  437.000000  Default  26.0000  26.0000
..         ...         ...         ...      ...      ...      ...
361     people   56.996357  617.607239   Topic5  -5.6698  -0.6406
117       time   52.643021  486.999451   Topic5  -5.7493  -0.4825
83         man   40.190186  191.571152   Topic5  -6.0192   0.1806
991        bad   37.049831  138.343414   Topic5  -6.1005   0.4248
123       come   39.484585  298.145630   Topic5  -6.0369  -0.2794

[442 rows x 6 columns], token_table=      Topic      Freq      Term
term                           
3291      1  0.764475      -&gt
3291      2  0.076447      -&gt
3291      4  0.076447      -&gt
7715      3  0.845738  -e&amp;h
7715      4  0.120820  -e&amp;h
...     ...       ...       ...
3049      2  0.866113       रहा
6491      3  0.868306         ⁣
4552      1  0.078827         ★
4552      2  0.078827         ★
4552      5  0.788268         ★

[1142 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[1, 4, 3, 2, 5])

###Hyperparameter Tuning 🔧

####Enhanced Model 1 (number of topics) 🦾


In [64]:
# Let's start with parameter tuning for the LDA model and,
# Increase number of topics to be used later to get to 
# Optimal number of distinct topics

# Define chunksize and passes

# Timing Start
model_1_program_start_time = time.time()

model_1 = LdaMulticore(corpus=corpus,
                       id2word=id2word,
                       num_topics=20,
                       random_state=42,
                       chunksize=2000,
                       passes=10)

# Timing End
model_1_program_end_time = time.time()


Streaming output truncated to the last 5000 lines.

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.

/usr/local/lib/python3.6/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.

/usr/local/lib/python3.6/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.

/usr/local/lib/python3.6/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.

/usr/local/lib/python3.6/dist-pa

In [65]:
#Printing First Model Time
model_1_runtime = round(model_1_program_end_time - model_1_program_start_time, 2)
print(model_1_runtime)


36.3963987827301


In [66]:
# Filtering for words 
words_1 = [re.findall(r'"([^"]*)"',t[1]) for t in model_1.print_topics()]

# Create Topics
topics_1 = [' '.join(t[0:10]) for t in words_1]

# Getting the topics
for id, t in enumerate(topics_1): 
    print(f"------ Topic {id} ------")
    print(t, end="\n\n")


------ Topic 0 ------
good love world friend week bad stay thank market card

------ Topic 1 ------
people right stop check go leave government pay give understand

------ Topic 2 ------
year money old feel school bring real 50 tomorrow problem

------ Topic 3 ------
look power believe americans kind = result virus bill dog

------ Topic 4 ------
need come video join house launch youtube live tag player

------ Topic 5 ------
way ktov crossover girl rise mean soon car pr come

------ Topic 6 ------
today 4 wait word night drop share de think little

------ Topic 7 ------
bitcoin state crypto care blah hope gift national response plan

------ Topic 8 ------
happen person find health face god lead learn truth say

------ Topic 9 ------
work help send woman long story allow twitter support weekend

------ Topic 10 ------
let time start end + high talk 24 low listen

------ Topic 11 ------
think new know guy case home death die country coronavirus

------ Topic 12 ------
hour rt free 5 oba

In [67]:
# Compute Perplexity
# a measure of how good the model is. lower the better
model_1_perplexity = model_1.log_perplexity(corpus)
print('\nPerplexity: ', model_1_perplexity) 

# Compute Coherence Score
coherence_model_1 = CoherenceModel(model=model_1, texts=df['lemma_tokens'], 
                                   dictionary=id2word, coherence='c_v')
coherence_lda_model_1 = coherence_model_1.get_coherence()
print('\nCoherence Score: ', coherence_lda_model_1)


Streaming output truncated to the last 5000 lines.

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.

/usr/local/lib/python3.6/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.

/usr/local/lib/python3.6/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.

/usr/local/lib/python3.6/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.

/usr/local/lib/python3.6/dist-pa


Perplexity:  -9.742035949658115

Coherence Score:  0.4138281791570699


In [68]:
#Creating Topic Distance Visualization 
pyLDAvis.enable_notebook()
pyLDAvis.gensim.prepare(model_1, corpus, id2word)

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
11    -0.104735 -0.162778       1        1  5.990582
15    -0.224099 -0.163714       2        1  5.697509
17     0.113547 -0.071264       3        1  5.501677
12    -0.119446 -0.151475       4        1  5.404756
7      0.012579 -0.026058       5        1  5.399176
1     -0.258681  0.059607       6        1  5.330340
8      0.108860 -0.017339       7        1  5.327854
14     0.087372 -0.050841       8        1  5.203998
9      0.087036  0.035708       9        1  5.185433
3      0.080033  0.005661      10        1  5.006906
16     0.039670  0.007109      11        1  4.959321
19    -0.144675  0.273276      12        1  4.949519
0     -0.019365  0.220492      13        1  4.923438
13     0.107904 -0.017247      14        1  4.879282
4      0.025935  0.031430      15        1  4.668213
18     0.040514  0.002698      16        1  4.423794
6      0.015763 -0.021975      17        1  4.415383
10     0.094475 -0.019558      18        1  4.407832
2      0.018925  0.057115      19        1  4.359571
5      0.038387  0.009152      20        1  3.965409, topic_info=              Term        Freq       Total Category  logprob  loglift
361         people  568.000000  568.000000  Default  30.0000  30.0000
605            let  404.000000  404.000000  Default  29.0000  29.0000
330             go  514.000000  514.000000  Default  28.0000  28.0000
63             day  456.000000  456.000000  Default  27.0000  27.0000
144           good  449.000000  449.000000  Default  26.0000  26.0000
...            ...         ...         ...      ...      ...      ...
2833  conservative   27.159037   28.020851  Topic20  -4.9258   3.1963
998           fake   25.496429   26.358244  Topic20  -4.9890   3.1943
3795       exactly   23.789780   24.651594  Topic20  -5.0582   3.1920
317           want   59.643513   87.527702  Topic20  -4.1391   2.8440
123           come   70.953842  342.740051  Topic20  -3.9655   1.6526

[710 rows x 6 columns], token_table=      Topic      Freq       Term
term                            
784      18  0.990496          +
72        3  0.995818          1
788       6  0.882385         10
788       8  0.105046         10
139       8  0.992869        100
...     ...       ...        ...
444      19  0.996625       year
157      12  0.984083        yes
1049     19  0.983717  yesterday
517      15  0.985903    youtube
4552      8  0.990949          ★

[723 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[12, 16, 18, 13, 8, 2, 9, 15, 10, 4, 17, 20, 1, 14, 5, 19, 7, 11, 3, 6])

####Model 2 (Increase Passes and define iterations)

In [69]:
#Change passes to asses if it'll improve coherence score
#passes = 50
model_2_program_start_time = time.time()

model_2 = LdaMulticore(corpus=corpus,
                       id2word=id2word,
                       num_topics=20,
                       random_state=42,
                       chunksize=2000,
                       passes=50,
                       iterations=100)

model_2_program_end_time = time.time()


Streaming output truncated to the last 5000 lines.

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.

/usr/local/lib/python3.6/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.

/usr/local/lib/python3.6/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.

/usr/local/lib/python3.6/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.

/usr/local/lib/python3.6/dist-pa

In [70]:
model_2_runtime = round(model_2_program_end_time - model_2_program_start_time, 2)
print(model_2_runtime, "seconds to finish")


179.17814183235168 seconds to finish


In [71]:
# Filtering for words 
words_2 = [re.findall(r'"([^"]*)"',t[1]) for t in model_2.print_topics()]

# Create Topics
topics_2 = [' '.join(t[0:10]) for t in words_2]

# Getting the topics
for id, t in enumerate(topics_2): 
    print(f"------ Topic {id} ------")
    print(t, end="\n\n")


------ Topic 0 ------
good love thank friend week bad stay market card x

------ Topic 1 ------
people right stop check go government leave give pay big

------ Topic 2 ------
year money old covid-19 feel school real bring project 50

------ Topic 3 ------
join power say americans ago kind = virus bill result

------ Topic 4 ------
need realdonaldtrump video buy house youtube tag player reach actually

------ Topic 5 ------
come long girl mean rise soon car better pr cause

------ Topic 6 ------
today world 4 wait ktov business word share drop night

------ Topic 7 ------
bitcoin crypto care hope national gift response plan trump important

------ Topic 8 ------
happen person health god face lead time glennjacobstn truth point

------ Topic 9 ------
help work woman post twitter story allow support weekend write

------ Topic 10 ------
let time start way end + talk 24 1 7

------ Topic 11 ------
think know new guy case home death coronavirus die country

------ Topic 12 ------
hour rt l

In [72]:
# Compute Perplexity
# a measure of how good the model is. lower the better
model_2_perplexity = model_2.log_perplexity(corpus)
print('\nPerplexity: ', model_2_perplexity) 

# Compute Coherence Score
coherence_model_2 = CoherenceModel(model=model_2, texts=df['lemma_tokens'], 
                                   dictionary=id2word, coherence='c_v')
coherence_lda_model_2 = coherence_model_2.get_coherence()
print('\nCoherence Score: ', coherence_lda_model_2)


Streaming output truncated to the last 5000 lines.

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.

/usr/local/lib/python3.6/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.

/usr/local/lib/python3.6/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.

/usr/local/lib/python3.6/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.

/usr/local/lib/python3.6/dist-pa


Perplexity:  -9.475841208321867

Coherence Score:  0.4133494959991747


In [73]:
#Creating Topic Distance Visualization 
pyLDAvis.enable_notebook()
pyLDAvis.gensim.prepare(model_2, corpus, id2word)


PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
11     0.123077  0.076178       1        1  5.941598
12     0.168776  0.042268       2        1  5.673605
17    -0.162326  0.193629       3        1  5.610148
7      0.067893 -0.025629       4        1  5.430728
1      0.213825  0.096874       5        1  5.370905
14    -0.100444  0.129875       6        1  5.306868
8     -0.107059  0.066487       7        1  5.158102
15     0.216097  0.108093       8        1  5.145818
9     -0.064354  0.033660       9        1  5.078068
16    -0.032351 -0.084722      10        1  5.039561
3     -0.044252 -0.092339      11        1  4.966994
0     -0.027048 -0.120875      12        1  4.934920
13    -0.081991 -0.032172      13        1  4.852873
10    -0.163957  0.178262      14        1  4.828273
19     0.102113 -0.012387      15        1  4.694767
6     -0.041282 -0.127425      16        1  4.694640
2     -0.015798 -0.139474      17        1  4.678837
4     -0.004565 -0.085660      18        1  4.411653
18    -0.028969 -0.109066      19        1  4.232094
5     -0.017385 -0.095579      20        1  3.949557, topic_info=              Term        Freq       Total Category  logprob  loglift
361         people  583.000000  583.000000  Default  30.0000  30.0000
144           good  448.000000  448.000000  Default  29.0000  29.0000
605            let  395.000000  395.000000  Default  28.0000  28.0000
330             go  500.000000  500.000000  Default  27.0000  27.0000
63             day  453.000000  453.000000  Default  26.0000  26.0000
...            ...         ...         ...      ...      ...      ...
998           fake   27.453510   28.314079  Topic20  -4.9110   3.2007
1071          shut   27.278330   28.138899  Topic20  -4.9174   3.2005
995            ass   27.146706   28.007275  Topic20  -4.9222   3.2004
2833  conservative   26.849615   27.710184  Topic20  -4.9332   3.2000
2832           bar   26.191874   27.052443  Topic20  -4.9580   3.1992

[708 rows x 6 columns], token_table=      Topic      Freq     Term
term                          
784      14  0.991018        +
72        3  0.636963        1
72       14  0.359646        1
788       5  0.734793       10
788       6  0.263209       10
...     ...       ...      ...
4031      9  0.981393      xrp
444      17  0.998021     year
157      15  0.988369      yes
517      18  0.987180  youtube
4552      6  0.993430        ★

[732 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[12, 13, 18, 8, 2, 15, 9, 16, 10, 17, 4, 1, 14, 11, 20, 7, 3, 5, 19, 6])

####Model 3 (Minimum probability)

In [93]:
model_3_program_start_time = time.time()

model_3 = LdaMulticore(corpus=corpus,
                       id2word=id2word,
                       num_topics=20,
                       random_state=42,
                       chunksize=2000,
                       passes=50,
                       minimum_probability=0.2, 
                       iterations=100)

model_3_program_end_time = time.time()


Streaming output truncated to the last 5000 lines.

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.

/usr/local/lib/python3.6/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.

/usr/local/lib/python3.6/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.

/usr/local/lib/python3.6/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.

/usr/local/lib/python3.6/dist-pa

In [0]:
model_3_runtime = round(model_3_program_end_time - model_3_program_start_time, 2)
print(model_3_runtime, "seconds to finish")


In [76]:
# Filtering for words 
words_2 = [re.findall(r'"([^"]*)"',t[1]) for t in model_2.print_topics()]

# Create Topics
topics_2 = [' '.join(t[0:10]) for t in words_2]

# Getting the topics
for id, t in enumerate(topics_2): 
    print(f"------ Topic {id} ------")
    print(t, end="\n\n")
    

------ Topic 0 ------
good love thank friend week bad stay market card x

------ Topic 1 ------
people right stop check go government leave give pay big

------ Topic 2 ------
year money old covid-19 feel school real bring project 50

------ Topic 3 ------
join power say americans ago kind = virus bill result

------ Topic 4 ------
need realdonaldtrump video buy house youtube tag player reach actually

------ Topic 5 ------
come long girl mean rise soon car better pr cause

------ Topic 6 ------
today world 4 wait ktov business word share drop night

------ Topic 7 ------
bitcoin crypto care hope national gift response plan trump important

------ Topic 8 ------
happen person health god face lead time glennjacobstn truth point

------ Topic 9 ------
help work woman post twitter story allow support weekend write

------ Topic 10 ------
let time start way end + talk 24 1 7

------ Topic 11 ------
think know new guy case home death coronavirus die country

------ Topic 12 ------
hour rt l

In [77]:
# Compute Perplexity
# a measure of how good the model is. lower the better
model_3_perplexity = model_3.log_perplexity(corpus)
print('\nPerplexity: ', model_3_perplexity) 

# Compute Coherence Score
coherence_model_3 = CoherenceModel(model=model_3, texts=df['lemma_tokens'], 
                                   dictionary=id2word, coherence='c_v')
coherence_lda_model_3 = coherence_model_3.get_coherence()
print('\nCoherence Score: ', coherence_lda_model_3)


Streaming output truncated to the last 5000 lines.

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.

/usr/local/lib/python3.6/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.

/usr/local/lib/python3.6/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.

/usr/local/lib/python3.6/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.

/usr/local/lib/python3.6/dist-pa


Perplexity:  -8.963115786917106

Coherence Score:  0.4985579012163873


In [78]:
#Creating Topic Distance Visualization 
pyLDAvis.enable_notebook()
pyLDAvis.gensim.prepare(model_2, corpus, id2word)


PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
11     0.123077  0.076178       1        1  5.940947
12     0.168776  0.042268       2        1  5.670873
17    -0.162326  0.193629       3        1  5.611416
7      0.067893 -0.025629       4        1  5.432084
1      0.213825  0.096874       5        1  5.370599
14    -0.100444  0.129875       6        1  5.306868
8     -0.107059  0.066487       7        1  5.157092
15     0.216097  0.108093       8        1  5.150209
9     -0.064354  0.033660       9        1  5.077988
16    -0.032351 -0.084722      10        1  5.039590
3     -0.044252 -0.092339      11        1  4.967000
0     -0.027048 -0.120875      12        1  4.931576
13    -0.081991 -0.032172      13        1  4.850658
10    -0.163957  0.178262      14        1  4.828255
6     -0.041282 -0.127425      15        1  4.694593
19     0.102113 -0.012387      16        1  4.693809
2     -0.015798 -0.139474      17        1  4.682174
4     -0.004565 -0.085660      18        1  4.412603
18    -0.028969 -0.109066      19        1  4.232101
5     -0.017385 -0.095579      20        1  3.949566, topic_info=              Term        Freq       Total Category  logprob  loglift
361         people  583.000000  583.000000  Default  30.0000  30.0000
144           good  447.000000  447.000000  Default  29.0000  29.0000
605            let  395.000000  395.000000  Default  28.0000  28.0000
330             go  500.000000  500.000000  Default  27.0000  27.0000
63             day  454.000000  454.000000  Default  26.0000  26.0000
...            ...         ...         ...      ...      ...      ...
998           fake   27.453581   28.314152  Topic20  -4.9110   3.2007
1071          shut   27.278400   28.138971  Topic20  -4.9174   3.2005
995            ass   27.146774   28.007345  Topic20  -4.9222   3.2004
2833  conservative   26.849684   27.710255  Topic20  -4.9332   3.2000
2832           bar   26.191940   27.052511  Topic20  -4.9580   3.1992

[708 rows x 6 columns], token_table=      Topic      Freq     Term
term                          
784      14  0.991022        +
72        3  0.636873        1
72       14  0.359595        1
788       5  0.734823       10
788       6  0.263220       10
...     ...       ...      ...
4031      9  0.981407      xrp
444      17  0.997311     year
157      16  0.988569      yes
517      18  0.986970  youtube
4552      6  0.993430        ★

[732 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[12, 13, 18, 8, 2, 15, 9, 16, 10, 17, 4, 1, 14, 11, 7, 20, 3, 5, 19, 6])

####Model 4 (alpha & eta)

In [79]:
model_4_start_time = time.time()

model_4 = LdaMulticore(corpus=corpus,
                       id2word=id2word,
                       num_topics=20,
                       random_state=42,
                       chunksize=2000,
                       passes=50,
                       minimum_probability=0.2, 
                       iterations=100,
                       alpha = 0.01,
                       eta=0.91)

model_4_end_time = time.time()


Streaming output truncated to the last 5000 lines.

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.

/usr/local/lib/python3.6/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.

/usr/local/lib/python3.6/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.

/usr/local/lib/python3.6/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.

/usr/local/lib/python3.6/dist-pa

In [88]:
model_4_runtime = round(model_4_end_time - model_4_start_time, 2)
print(model_4_runtime, "seconds to finish")


219.39 seconds to finish


In [81]:
# Filtering for words 
words_2 = [re.findall(r'"([^"]*)"',t[1]) for t in model_2.print_topics()]

# Create Topics
topics_2 = [' '.join(t[0:10]) for t in words_2]

# Getting the topics
for id, t in enumerate(topics_2): 
    print(f"------ Topic {id} ------")
    print(t, end="\n\n")
    

------ Topic 0 ------
good love thank friend week bad stay market card x

------ Topic 1 ------
people right stop check go government leave give pay big

------ Topic 2 ------
year money old covid-19 feel school real bring project 50

------ Topic 3 ------
join power say americans ago kind = virus bill result

------ Topic 4 ------
need realdonaldtrump video buy house youtube tag player reach actually

------ Topic 5 ------
come long girl mean rise soon car better pr cause

------ Topic 6 ------
today world 4 wait ktov business word share drop night

------ Topic 7 ------
bitcoin crypto care hope national gift response plan trump important

------ Topic 8 ------
happen person health god face lead time glennjacobstn truth point

------ Topic 9 ------
help work woman post twitter story allow support weekend write

------ Topic 10 ------
let time start way end + talk 24 1 7

------ Topic 11 ------
think know new guy case home death coronavirus die country

------ Topic 12 ------
hour rt l

In [82]:
# Compute Perplexity
# a measure of how good the model is. lower the better
model_4_perplexity = model_4.log_perplexity(corpus)
print('\nPerplexity: ', model_4_perplexity) 

# Compute Coherence Score
coherence_model_4 = CoherenceModel(model=model_4, texts=df['lemma_tokens'], 
                                   dictionary=id2word, coherence='c_v')
coherence_lda_model_4 = coherence_model_4.get_coherence()
print('\nCoherence Score: ', coherence_lda_model_4)


Streaming output truncated to the last 5000 lines.

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.

/usr/local/lib/python3.6/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.

/usr/local/lib/python3.6/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.

/usr/local/lib/python3.6/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning:

Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.

/usr/local/lib/python3.6/dist-pa


Perplexity:  -8.870009298561314

Coherence Score:  0.5311231452909411


In [83]:
#Creating Topic Distance Visualization 
pyLDAvis.enable_notebook()
pyLDAvis.gensim.prepare(model_2, corpus, id2word)


PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
11     0.123077  0.076178       1        1  5.938909
12     0.168776  0.042268       2        1  5.673769
17    -0.162326  0.193629       3        1  5.608974
7      0.067893 -0.025629       4        1  5.432081
1      0.213825  0.096874       5        1  5.368528
14    -0.100444  0.129875       6        1  5.306875
8     -0.107059  0.066487       7        1  5.156772
15     0.216097  0.108093       8        1  5.149316
9     -0.064354  0.033660       9        1  5.077886
16    -0.032351 -0.084722      10        1  5.039603
3     -0.044252 -0.092339      11        1  4.967000
0     -0.027048 -0.120875      12        1  4.933921
13    -0.081991 -0.032172      13        1  4.850652
10    -0.163957  0.178262      14        1  4.829787
19     0.102113 -0.012387      15        1  4.696389
6     -0.041282 -0.127425      16        1  4.694627
2     -0.015798 -0.139474      17        1  4.679831
4     -0.004565 -0.085660      18        1  4.412583
18    -0.028969 -0.109066      19        1  4.232922
5     -0.017385 -0.095579      20        1  3.949569, topic_info=              Term        Freq       Total Category  logprob  loglift
361         people  582.000000  582.000000  Default  30.0000  30.0000
144           good  448.000000  448.000000  Default  29.0000  29.0000
605            let  395.000000  395.000000  Default  28.0000  28.0000
330             go  500.000000  500.000000  Default  27.0000  27.0000
63             day  453.000000  453.000000  Default  26.0000  26.0000
...            ...         ...         ...      ...      ...      ...
998           fake   27.453596   28.314173  Topic20  -4.9110   3.2007
1071          shut   27.278414   28.138990  Topic20  -4.9174   3.2005
995            ass   27.146790   28.007366  Topic20  -4.9222   3.2004
2833  conservative   26.849699   27.710276  Topic20  -4.9332   3.2000
2832           bar   26.191954   27.052530  Topic20  -4.9580   3.1992

[708 rows x 6 columns], token_table=      Topic      Freq     Term
term                          
784      14  0.990710        +
72        3  0.636976        1
72       14  0.359653        1
788       5  0.735030       10
788       6  0.263294       10
...     ...       ...      ...
4031      9  0.981427      xrp
444      17  0.997809     year
157      15  0.988032      yes
517      18  0.986974  youtube
4552      6  0.993429        ★

[732 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[12, 13, 18, 8, 2, 15, 9, 16, 10, 17, 4, 1, 14, 11, 20, 7, 3, 5, 19, 6])

###Progress Tracksheet 🧑‍🔬

In [86]:
TS = {'model': ["base", 1, 2, 3, 4], 
      'runtime_seconds': [base_model_runtime, model_1_runtime,
                 model_2_runtime, model_3_runtime, model_4_runtime],
      'coherence_score': [coherence_lda_model_base, coherence_lda_model_1,
                          coherence_lda_model_2, coherence_lda_model_3, 
                          coherence_lda_model_4],
      'Perplexity': [base_perplexity, model_1_perplexity, model_2_perplexity,
                     model_3_perplexity, model_4_perplexity]}

track_sheet = pd.DataFrame(data=TS)

track_sheet.head()

model  runtime_seconds  coherence_score  Perplexity
0  base     2.525027e+01         0.171768   -8.453721
1     1     3.639640e+01         0.413828   -9.742036
2     2     1.791781e+02         0.413349   -9.475841
3     3     1.591744e+09         0.498558   -8.963116
4     4     2.193909e+02         0.531123   -8.870009

In [87]:
track_sheet['runtime_seconds'][0]

25.250271320343018

In [0]:
Track_Sheet.dtypes